### Лабораторная работа по курсу Feature engineering

**Задание** Лабораторная работа
=====================

Цель лабораторной работы получить практические знания по работе с признаками на известном датасете статистики самоубийств.

Вам необходимо будет подготовить данные для обучения линейной модели предсказания количества самоубийств (столбец - suicides/100k pop).

Чек-лист:
0. Изучите файл annotation.txt. Там содержится информация о датасете.
1. Загрузите датасет data.csv.
2. Посмотрите на данные. Отобразите общую информацию по признакам (вспомните о describe и info). Напишите в markdown свои наблюдения.
3. Выявите пропуски, а также возможные причины их возникновения. Решите, что следует сделать с ними. Напишите в markdown свои наблюдения.
4. Оцените зависимости переменных между собой. Используйте корреляции. Будет хорошо, если воспользуетесь profile_report. Напишите в markdown свои наблюдения.
5. Определите стратегию преобразования категориальных признаков (т.е. как их сделать адекватными для моделей).
6. Найдите признаки, которые можно разделить на другие, или преобразовать в другой тип данных. Удалите лишние, при необходимости.
7. Разделите выборку на обучаемую и тестовую.
8. Обучите линейную модель. Напишите в markdown свои наблюдения по полученным результатам.

Если возникнут затруднения, то смотрите на материал практических занятий. Данного там должно хватить для выполнения всех пунктов. Желаю успеха!

In [48]:
import pandas as pd
import numpy as np
import seaborn as sns
from matplotlib import pyplot as plt

In [49]:
import pandas_profiling

In [50]:
df = pd.read_csv('лабораторная/data.csv')
df.head()

sex          age  suicides_no  population  suicides/100k pop  \
0    male  15-24 years           21      312900               6.71   
1    male  35-54 years           16      308000               5.19   
2  female  15-24 years           14      289700               4.83   
3    male    75+ years            1       21800               4.59   
4    male  25-34 years            9      274300               3.28   

  country-year  HDI for year  gdp_for_year ($)   gdp_per_capita ($)  \
0  Albania1987           NaN      2,156,624,900                 796   
1  Albania1987           NaN      2,156,624,900                 796   
2  Albania1987           NaN      2,156,624,900                 796   
3  Albania1987           NaN      2,156,624,900                 796   
4  Albania1987           NaN      2,156,624,900                 796   

        generation  
0     Generation X  
1           Silent  
2     Generation X  
3  G.I. Generation  
4          Boomers

In [51]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 27820 entries, 0 to 27819
Data columns (total 10 columns):
sex                   27820 non-null object
age                   27820 non-null object
suicides_no           27820 non-null int64
population            27820 non-null int64
suicides/100k pop     27820 non-null float64
country-year          27820 non-null object
HDI for year          8364 non-null float64
 gdp_for_year ($)     27820 non-null object
gdp_per_capita ($)    27820 non-null int64
generation            27820 non-null object
dtypes: float64(2), int64(3), object(5)
memory usage: 2.1+ MB


In [52]:
df.columns

Index(['sex', 'age', 'suicides_no', 'population', 'suicides/100k pop',
       'country-year', 'HDI for year', ' gdp_for_year ($) ',
       'gdp_per_capita ($)', 'generation'],
      dtype='object')

In [53]:
df.profile_report()

У нас датасет из 10 переменных. 
'sex' - надо изменить в другой тип
'age' - содержит категорийные данные, для обработки надо будет их модифицировать
'suicides_no' - возможная целевая переменная
'population' - данные, на первый взгляд, в хорошем состоянии
'suicides/100k_pop' - еще более подходящая целевая переменная
'country-year' - надо обработать даные, разделить наименование страны и год
'HDI_for_year' - полезный индикатор (индекс человеческого развития) видно, что без обработки он показывает корреляции, проблема в том, что слишком велико количество отсутствующих значений. Столбец надо убирать
'_gdp_for_year_($)_' - необходимо будет изменить тип в numeric
'gdp_per_capita_($)'- данные, на первый взгляд, в хорошем состоянии. Они даже более приемнимы, чем ВВП в абсолютном выражении
'generation' - могут быть полезны, надо изменить тип и затем использовать OHE

In [55]:
df['sex'] = df['sex'].astype(str)
df['generation'] = df['generation'].astype(str)
df['country'] = df['country-year'].str[:-4]
df['year'] = df['country-year'].str[-4:].astype(int)
df.head()
df.tail()
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 27820 entries, 0 to 27819
Data columns (total 12 columns):
sex                   27820 non-null object
age                   27820 non-null object
suicides_no           27820 non-null int64
population            27820 non-null int64
suicides/100k_pop     27820 non-null float64
country-year          27820 non-null object
HDI_for_year          8364 non-null float64
_gdp_for_year_($)_    27820 non-null object
gdp_per_capita_($)    27820 non-null int64
generation            27820 non-null object
country               27820 non-null object
year                  27820 non-null int32
dtypes: float64(2), int32(1), int64(3), object(6)
memory usage: 2.4+ MB


In [56]:
df['age'].unique()

array(['15-24 years', '35-54 years', '75+ years', '25-34 years',
       '55-74 years', '5-14 years'], dtype=object)

In [57]:
def age_cat(a):
    if a == '5-14 years':
        return 'gr_1'
    elif a == '15-24 years':
        return 'gr_2'
    elif a == '25-34 years':
        return 'gr_3'
    elif a == '35-54 years':
        return 'gr_4'
    elif a == '55-74 years':
        return 'gr_5'
    elif a == '75+ years':
        return 'gr_6'
    else:
        return 'missing'

In [58]:
df['age_group'] = df.age.apply(age_cat).astype(str)
df.head()

sex          age  suicides_no  population  suicides/100k_pop  \
0    male  15-24 years           21      312900               6.71   
1    male  35-54 years           16      308000               5.19   
2  female  15-24 years           14      289700               4.83   
3    male    75+ years            1       21800               4.59   
4    male  25-34 years            9      274300               3.28   

  country-year  HDI_for_year _gdp_for_year_($)_  gdp_per_capita_($)  \
0  Albania1987           NaN      2,156,624,900                 796   
1  Albania1987           NaN      2,156,624,900                 796   
2  Albania1987           NaN      2,156,624,900                 796   
3  Albania1987           NaN      2,156,624,900                 796   
4  Albania1987           NaN      2,156,624,900                 796   

        generation  country  year age_group  
0     Generation X  Albania  1987      gr_2  
1           Silent  Albania  1987      gr_4  
2     Generation X  Albania  1987      gr_2  
3  G.I. Generation  Albania  1987      gr_6  
4          Boomers  Albania  1987      gr_3

In [59]:
df.columns

Index(['sex', 'age', 'suicides_no', 'population', 'suicides/100k_pop',
       'country-year', 'HDI_for_year', '_gdp_for_year_($)_',
       'gdp_per_capita_($)', 'generation', 'country', 'year', 'age_group'],
      dtype='object')

In [60]:
dfm = df[['sex', 'suicides/100k_pop', 'gdp_per_capita_($)', 'generation', 'country', 'year', 'age_group']]
dfm.head()

sex  suicides/100k_pop  gdp_per_capita_($)       generation  country  \
0    male               6.71                 796     Generation X  Albania   
1    male               5.19                 796           Silent  Albania   
2  female               4.83                 796     Generation X  Albania   
3    male               4.59                 796  G.I. Generation  Albania   
4    male               3.28                 796          Boomers  Albania   

   year age_group  
0  1987      gr_2  
1  1987      gr_4  
2  1987      gr_2  
3  1987      gr_6  
4  1987      gr_3

In [61]:
dfm.profile_report()

Мы еще видим, что переменные 'age_group' и 'generation' имеют 100% корреляцию, то есть, это два наименования одного и того же признака. Оставим только одну из колонок.

In [62]:
dfm = dfm[['sex', 'suicides/100k_pop', 'gdp_per_capita_($)', 'country', 'year', 'age_group']]
dfm.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 27820 entries, 0 to 27819
Data columns (total 6 columns):
sex                   27820 non-null object
suicides/100k_pop     27820 non-null float64
gdp_per_capita_($)    27820 non-null int64
country               27820 non-null object
year                  27820 non-null int32
age_group             27820 non-null object
dtypes: float64(1), int32(1), int64(1), object(3)
memory usage: 1.2+ MB


Проверим, может, чудесным образом модель сработает на имеющихся числовых значениях.

In [65]:
from sklearn import preprocessing
from sklearn.model_selection import train_test_split

In [70]:
X = dfm[['gdp_per_capita_($)', 'year']]
y = dfm[['suicides/100k_pop']]

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=30)


In [71]:
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score

estimator = LinearRegression()
estimator.fit(X_train, y_train) 


y_pred = estimator.predict(X_test)

print("R2: \t", r2_score(y_test, y_pred))
print("RMSE: \t", np.sqrt(mean_squared_error(y_test, y_pred)))
print("MAE: \t", mean_absolute_error(y_test, y_pred))

R2: 	 0.0028515776725720476
RMSE: 	 18.766716012819035
MAE: 	 12.431848243851151


Чуда не случилось, что, конечно, было ожидаемо.

Обрабатываем категориальные признаки. Попробуем сначала обойтись без страны, а только добавить пол и возрастную группу.

In [79]:
sex = dfm['sex'].get_values().reshape(-1, 1)
age_group = dfm['age_group'].get_values().reshape(-1, 1)

In [76]:
oh_encoder1 = preprocessing.OneHotEncoder()
oh_encoder1.fit(sex)
oh_result1 = oh_encoder1.transform(sex).toarray()
oh_result1

array([[0., 1.],
       [0., 1.],
       [1., 0.],
       ...,
       [0., 1.],
       [1., 0.],
       [1., 0.]])

In [80]:
oh_encoder2 = preprocessing.OneHotEncoder()
oh_encoder2.fit(age_group)
oh_result2 = oh_encoder2.transform(age_group).toarray()
oh_result2

array([[0., 1., 0., 0., 0., 0.],
       [0., 0., 0., 1., 0., 0.],
       [0., 1., 0., 0., 0., 0.],
       ...,
       [1., 0., 0., 0., 0., 0.],
       [1., 0., 0., 0., 0., 0.],
       [0., 0., 0., 0., 1., 0.]])

In [91]:
sex_columns = ['sex_{}'.format(i) for i in range(oh_result1.shape[1])]
sex_df = pd.DataFrame(oh_result1, columns=sex_columns)
sex_df.index = dfm.index
dfm_sex = pd.concat([dfm, sex_df], axis=1)
dfm_sex = dfm_sex.drop(['sex'], axis=1)
dfm_sex.head()

suicides/100k_pop  gdp_per_capita_($)  country  year age_group  sex_0  \
0               6.71                 796  Albania  1987      gr_2    0.0   
1               5.19                 796  Albania  1987      gr_4    0.0   
2               4.83                 796  Albania  1987      gr_2    1.0   
3               4.59                 796  Albania  1987      gr_6    0.0   
4               3.28                 796  Albania  1987      gr_3    0.0   

   sex_1  
0    1.0  
1    1.0  
2    0.0  
3    1.0  
4    1.0

In [92]:
age_gr_columns = ['age_gr_{}'.format(i) for i in range(oh_result2.shape[1])]
age_gr_df = pd.DataFrame(oh_result2, columns=age_gr_columns)
age_gr_df.index = dfm.index
dfm_sex_age_gr = pd.concat([dfm_sex, age_gr_df], axis=1)
dfm_sex_age_gr = dfm_sex_age_gr.drop(['age_group'], axis=1)

In [94]:
dfm_sex_age_gr.head()

suicides/100k_pop  gdp_per_capita_($)  country  year  sex_0  sex_1  \
0               6.71                 796  Albania  1987    0.0    1.0   
1               5.19                 796  Albania  1987    0.0    1.0   
2               4.83                 796  Albania  1987    1.0    0.0   
3               4.59                 796  Albania  1987    0.0    1.0   
4               3.28                 796  Albania  1987    0.0    1.0   

   age_gr_0  age_gr_1  age_gr_2  age_gr_3  age_gr_4  age_gr_5  
0       0.0       1.0       0.0       0.0       0.0       0.0  
1       0.0       0.0       0.0       1.0       0.0       0.0  
2       0.0       1.0       0.0       0.0       0.0       0.0  
3       0.0       0.0       0.0       0.0       0.0       1.0  
4       0.0       0.0       1.0       0.0       0.0       0.0

In [95]:
X = dfm_sex_age_gr.drop(['country'], axis=1)
y = dfm_sex_age_gr['suicides/100k_pop']

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=30)

estimator = LinearRegression()
estimator.fit(X_train, y_train) 

y_pred = estimator.predict(X_test)

print("R2: \t", r2_score(y_test, y_pred))
print("RMSE: \t", np.sqrt(mean_squared_error(y_test, y_pred)))
print("MAE: \t", mean_absolute_error(y_test, y_pred))

R2: 	 1.0
RMSE: 	 2.2300870829879044e-12
MAE: 	 1.6688229925444586e-12


Мы видим, что на основании показателей пола, возрастной группы, года, ВВП на душу населения предсказание модели совершенное.